# VQE algorithm study

## Problem

In [167]:
# Create the qubit-Hamiltonian for ·OH molecule

from qiskit_nature.units import DistanceUnit
from qiskit_nature.second_q.drivers import PySCFDriver, Psi4Driver
from qiskit_nature.second_q.mappers import JordanWignerMapper,ParityMapper,BravyiKitaevMapper,QubitMapper

with open(".pyscf_conf.py", "w") as f:
    f.write("B3LYP_WITH_VWN5 = True")

mol_geometry = """
O 0.0 0.0 0.0
H 0.45 -0.1525 -0.8454
"""

driver = PySCFDriver(
    atom=mol_geometry.strip(),
    basis='sto3g',
    charge=1,
    spin=0,
    unit=DistanceUnit.ANGSTROM
)


qmolecule = driver.run()
hamiltonian = qmolecule.hamiltonian
second_q_ham = hamiltonian.second_q_op()
qubit_ham = JordanWignerMapper().map(second_q_ham)

print(qubit_ham.num_qubits, "qubits in the Hamiltonian.")

12 qubits in the Hamiltonian.


## Circuit Design

Hardware efficient ansatz

- [Efficient SU2 2-local circuit](###Efficient-SU2-2-local-circuit-(qiskit.circuit.library))
- [Excitation preserving circuit](###Excitation-preserving-circuit-(qiskit.circuit.library))
- [Pauli 2-design ansatz](###Pauli-Two-Design-ansatz-(qiskit.circuit.library))

Problem inspired ansatz

- Unitary cluster coupling (UCC)
- ADAPT

Circuit search

- Quantum noise-adaptive-search
- Quantum architecture search


In [168]:
# Get hardware backends

from huayi_providers.fake_huayi import FakeHuayi
from qiskit_ionq import IonQProvider
from qiskit.providers.fake_provider import *
from qiskit_aer.noise.noise_model import NoiseModel

# "fakeionq" is de facto a generic backend with all kinds of gates
fakehuayi = FakeHuayi()
fakeionq = IonQProvider().get_backend("ionq_simulator")
fakemontreal = FakeMontreal()

### Efficient SU2 2-local circuit (qiskit.circuit.library)

The ``EfficientSU2`` circuit consists of layers of single qubit operations spanned by SU(2) and ``CX`` entanglements.

This is a heuristic pattern that can be used to prepare trial wave functions for variational quantum algorithms or classification circuit for machine learning.

``su2_gates`` includes the parametric single-qubit gates applied to each qubit.

``entanglement`` determines how to connect the qubits for ``CX`` operations.

Tecent Quantum Lab uses the similar ansatz bysetting ``su2_gates=['ry']``

In [169]:
from qiskit.circuit.library import EfficientSU2
from qiskit import transpile
from qiskit import QuantumCircuit

n_qubits = 8
ent_pairs = [[i, i+1] for i in range(0,n_qubits,2)] + \
            [[i-1, i] for i in range(2,n_qubits,2)]
ansatz_effsu2 = EfficientSU2(n_qubits, 
                             su2_gates=['ry'], 
                             entanglement=ent_pairs, 
                             reps=1,flatten=True)
# c = QuantumCircuit(n_qubits)
# c.compose(ansatz_effsu2, inplace=True)
# for i in range(n_qubits):
#     if i != 0 and i != 4:
#         c.x(i)

print("Efficient SU2 ansatz")
print(ansatz_effsu2.draw(fold=400, idle_wires=False))

c_montreal = transpile(ansatz_effsu2, backend=fakemontreal, optimization_level=3)
print("Transpileed with Montreal backend, depth = {}".format(c_montreal.depth()))
print(c_montreal.draw(fold=160, idle_wires=False))

c_huayi = transpile(ansatz_effsu2, backend=fakehuayi, optimization_level=3)
print("Transpileed with Huayi backend, depth = {}".format(c_huayi.depth()))
print(c_huayi.draw(fold=400, idle_wires=False))

Efficient SU2 ansatz
     ┌──────────┐      ┌──────────┐             
q_0: ┤ Ry(θ[0]) ├──■───┤ Ry(θ[8]) ├─────────────
     ├──────────┤┌─┴─┐ └──────────┘ ┌──────────┐
q_1: ┤ Ry(θ[1]) ├┤ X ├──────■───────┤ Ry(θ[9]) ├
     ├──────────┤└───┘    ┌─┴─┐    ┌┴──────────┤
q_2: ┤ Ry(θ[2]) ├──■──────┤ X ├────┤ Ry(θ[10]) ├
     ├──────────┤┌─┴─┐    └───┘    ├───────────┤
q_3: ┤ Ry(θ[3]) ├┤ X ├──────■──────┤ Ry(θ[11]) ├
     ├──────────┤└───┘    ┌─┴─┐    ├───────────┤
q_4: ┤ Ry(θ[4]) ├──■──────┤ X ├────┤ Ry(θ[12]) ├
     ├──────────┤┌─┴─┐    └───┘    ├───────────┤
q_5: ┤ Ry(θ[5]) ├┤ X ├──────■──────┤ Ry(θ[13]) ├
     ├──────────┤└───┘    ┌─┴─┐    ├───────────┤
q_6: ┤ Ry(θ[6]) ├──■──────┤ X ├────┤ Ry(θ[14]) ├
     ├──────────┤┌─┴─┐┌───┴───┴───┐└───────────┘
q_7: ┤ Ry(θ[7]) ├┤ X ├┤ Ry(θ[15]) ├─────────────
     └──────────┘└───┘└───────────┘             
Transpileed with Montreal backend, depth = 10
          ┌────┐┌──────────────┐┌────┐┌────────┐     ┌────┐┌──────────────┐      ┌────┐         ┌───

### Excitation Preserving circuit (qiskit.circuit.library)

The ``ExcitationPreserving`` circuit preserves the ratio of $|00\rangle$, $|01\rangle +|10\rangle $ and $|11\rangle $ states. To this end, this circuit
uses two-qubit interactions of the form
$$  \begin{pmatrix}
    1 & 0 & 0 & 0 \\
    0 & \cos\left(\theta/2\right) & -i\sin\left(\theta/2\right) & 0 \\
    0 & -i\sin\left(\theta/2\right) & \cos\left(\theta/2\right) & 0 \\
    0 & 0 & 0 & e^{-i\phi} 
    \end{pmatrix} $$
for the mode ``'fsim'`` or with $e^{-i\phi} = 1$ for the mode ``'iswap'``.



In [4]:
from qiskit.circuit.library import ExcitationPreserving

ansatz_EP = ExcitationPreserving(n_qubits, 
                              reps=1, 
                              mode='fsim', 
                              entanglement=ent_pairs, 
                              insert_barriers=True,
                              flatten=True
                             )


print("Excitation Preserving ansatz")
print(ansatz_EP.draw(fold=400, idle_wires=False))

c_montreal = transpile(ansatz_EP, backend=fakemontreal, optimization_level=3)
print("Transpileed with Montreal backend, depth = {}".format(c_montreal.depth()))
print(c_montreal.draw(fold=160, idle_wires=False))

c_huayi = transpile(ansatz_EP, backend=fakehuayi, optimization_level=3)
print("Transpileed with Huayi backend, depth = {}".format(c_huayi.depth()))
print(c_huayi.draw(fold=160, idle_wires=False))

Excitation Preserving ansatz
     ┌──────────┐ ░  ┌────────────┐ ┌────────────┐                                                     ░ ┌───────────┐
q_0: ┤ Rz(θ[0]) ├─░──┤0           ├─┤0           ├──■──────────────────────────────────────────────────░─┤ Rz(θ[22]) ├
     ├──────────┤ ░  │  Rxx(θ[8]) │ │  Ryy(θ[8]) │  │P(θ[9]) ┌─────────────┐┌─────────────┐            ░ ├───────────┤
q_1: ┤ Rz(θ[1]) ├─░──┤1           ├─┤1           ├──■────────┤0            ├┤0            ├─■──────────░─┤ Rz(θ[23]) ├
     ├──────────┤ ░ ┌┴────────────┤┌┴────────────┤           │  Rxx(θ[16]) ││  Ryy(θ[16]) │ │P(θ[17])  ░ ├───────────┤
q_2: ┤ Rz(θ[2]) ├─░─┤0            ├┤0            ├─■─────────┤1            ├┤1            ├─■──────────░─┤ Rz(θ[24]) ├
     ├──────────┤ ░ │  Rxx(θ[10]) ││  Ryy(θ[10]) │ │P(θ[11]) ├─────────────┤├─────────────┤            ░ ├───────────┤
q_3: ┤ Rz(θ[3]) ├─░─┤1            ├┤1            ├─■─────────┤0            ├┤0            ├─■──────────░─┤ Rz(θ[25]) ├
     ├──────────┤ ░

### Pauli Two-Design ansatz (qiskit.circuit.library)

This class implements a particular form of a 2-design circuit, which is frequently studied in quantum machine learning literature, such as e.g. the investigating of Barren plateaus in variational algorithms.

The circuit consists of alternating rotation and entanglement layers with an initial layer of $\sqrt{H} = RY(\pi/4)$ gates.
The rotation layers contain single qubit Pauli rotations, where the axis is chosen uniformly at random to be ``X``, ``Y`` or ``Z``.
The entanglement layers is compromised of pairwise ``CZ`` gates with a total depth of 2.

In [5]:
from qiskit.circuit.library import PauliTwoDesign

ansatz_pauli2des = PauliTwoDesign(n_qubits, 
                                  reps=2,
                                  seed=120,
                                  insert_barriers=True
                                  )
ansatz_pauli2des._flatten=True

print("Pauli Two-Design ansatz")
print(ansatz_pauli2des.draw(fold=160, idle_wires=False))

c_montreal = transpile(ansatz_pauli2des, backend=fakemontreal, optimization_level=3)
print("Transpileed with Montreal backend, depth = {}".format(c_montreal.depth()))
print(c_montreal.draw(fold=160, idle_wires=False))

c_huayi = transpile(ansatz_pauli2des, backend=fakehuayi, optimization_level=3)
print("Transpileed with Huayi backend, depth = {}".format(c_huayi.depth()))
print(c_huayi.draw(fold=160, idle_wires=False))

Pauli Two-Design ansatz
     ┌─────────┐ ░ ┌──────────┐       ░  ┌──────────┐       ░ ┌───────────┐
q_0: ┤ Ry(π/4) ├─░─┤ Rx(θ[0]) ├─■─────░──┤ Ry(θ[8]) ├─■─────░─┤ Rx(θ[16]) ├
     ├─────────┤ ░ ├──────────┤ │     ░  ├──────────┤ │     ░ ├───────────┤
q_1: ┤ Ry(π/4) ├─░─┤ Rz(θ[1]) ├─■──■──░──┤ Ry(θ[9]) ├─■──■──░─┤ Rz(θ[17]) ├
     ├─────────┤ ░ ├──────────┤    │  ░ ┌┴──────────┤    │  ░ ├───────────┤
q_2: ┤ Ry(π/4) ├─░─┤ Rx(θ[2]) ├─■──■──░─┤ Ry(θ[10]) ├─■──■──░─┤ Ry(θ[18]) ├
     ├─────────┤ ░ ├──────────┤ │     ░ ├───────────┤ │     ░ ├───────────┤
q_3: ┤ Ry(π/4) ├─░─┤ Rx(θ[3]) ├─■──■──░─┤ Ry(θ[11]) ├─■──■──░─┤ Ry(θ[19]) ├
     ├─────────┤ ░ ├──────────┤    │  ░ ├───────────┤    │  ░ ├───────────┤
q_4: ┤ Ry(π/4) ├─░─┤ Ry(θ[4]) ├─■──■──░─┤ Rx(θ[12]) ├─■──■──░─┤ Ry(θ[20]) ├
     ├─────────┤ ░ ├──────────┤ │     ░ ├───────────┤ │     ░ ├───────────┤
q_5: ┤ Ry(π/4) ├─░─┤ Rx(θ[5]) ├─■──■──░─┤ Ry(θ[13]) ├─■──■──░─┤ Rx(θ[21]) ├
     ├─────────┤ ░ ├──────────┤    │  ░ ├───────────┤    │  ░ ├─

### UCC(SD) ansatz (qiskit_nature.second_q.circuit.library)

The UCC(SD) ansatz builder requires the molecle information

In [74]:
from qiskit_nature.second_q.circuit.library import UCCSD, HartreeFock
from qiskit_aer.backends.aer_simulator import AerSimulator

uccsd_ansatz = UCCSD(
    qmolecule.num_spatial_orbitals,
    qmolecule.num_particles,
    JordanWignerMapper(),
    initial_state=HartreeFock(
        qmolecule.num_spatial_orbitals,
        qmolecule.num_particles,
        JordanWignerMapper(),
    ),
)

uccsd_lv0 = transpile(uccsd_ansatz, AerSimulator(), optimization_level=0)
uccsd_lv1 = transpile(uccsd_ansatz, AerSimulator(), optimization_level=1)
uccsd_lv2 = transpile(uccsd_ansatz, AerSimulator(), optimization_level=2)
uccsd_lv3 = transpile(uccsd_ansatz, AerSimulator(), optimization_level=3)
print("=== Circuit Depth ===")
print("Level 0 : {}".format( uccsd_lv0.depth() ))
print("Level 1 : {}".format( uccsd_lv1.depth() ))
print("Level 2 : {}".format( uccsd_lv2.depth() ))
print("Level 3 : {}".format( uccsd_lv3.depth() ))
print("=== Level 3 Circuit ===")
uccsd_lv3.draw(fold=120)

=== Circuit Depth ===
Level 0 : 10388
Level 1 : 10388
Level 2 : 8380
Level 3 : 8380
=== Level 3 Circuit ===


global phase: 3π/2
      ┌─────────────┐               ┌───┐┌──────────────┐┌───┐┌──────────────┐                                         »
 q_0: ┤ U2(-π,-π/2) ├───────────────┤ X ├┤ Rz(1.0*t[0]) ├┤ X ├┤ U2(-π/2,π/2) ├─────────────────────────────────────────»
      └┬────────────┤          ┌───┐└─┬─┘└──────────────┘└─┬─┘└────┬───┬─────┘                                    ┌───┐»
 q_1: ─┤ U3(π,-π,0) ├──────────┤ X ├──■────────────────────■───────┤ X ├──────────────────────────────────────────┤ X ├»
       ├────────────┤     ┌───┐└─┬─┘                               └─┬─┘      ┌───┐                          ┌───┐└─┬─┘»
 q_2: ─┤ U3(π,-π,0) ├─────┤ X ├──■───────────────────────────────────■────────┤ X ├──────────────────────────┤ X ├──■──»
       ├────────────┤┌───┐└─┬─┘                                               └─┬─┘┌───┐                ┌───┐└─┬─┘     »
 q_3: ─┤ U3(π,-π,0) ├┤ X ├──■───────────────────────────────────────────────────■──┤ X ├────────────────┤ X ├──■───────»
       └┬──────────┬┘└─┬─┘                                                         └─┬─┘┌──────────────┐└─┬─┘          »
 q_4: ──┤ U2(0,-π) ├───■─────────────────────────────────────────────────────────────■──┤ U2(π/2,-π/2) ├──■────────────»
        ├──────────┤                                                                    └──────────────┘               »
 q_5: ──┤ U2(0,-π) ├───────────────────────────────────────────────────────────────────────────────────────────────────»
      ┌─┴──────────┴┐               ┌───┐┌──────────────┐┌───┐┌──────────────┐                                         »
 q_6: ┤ U2(-π,-π/2) ├───────────────┤ X ├┤ Rz(1.0*t[8]) ├┤ X ├┤ U2(-π/2,π/2) ├─────────────────────────────────────────»
      └┬────────────┤          ┌───┐└─┬─┘└──────────────┘└─┬─┘└────┬───┬─────┘                                    ┌───┐»
 q_7: ─┤ U3(π,-π,0) ├──────────┤ X ├──■────────────────────■───────┤ X ├──────────────────────────────────────────┤ X ├»
       ├────────────┤     ┌───┐└─┬─┘                               └─┬─┘      ┌───┐                          ┌───┐└─┬─┘»
 q_8: ─┤ U3(π,-π,0) ├─────┤ X ├──■───────────────────────────────────■────────┤ X ├──────────────────────────┤ X ├──■──»
       ├────────────┤┌───┐└─┬─┘                                               └─┬─┘┌───┐                ┌───┐└─┬─┘     »
 q_9: ─┤ U3(π,-π,0) ├┤ X ├──■───────────────────────────────────────────────────■──┤ X ├────────────────┤ X ├──■───────»
       └┬──────────┬┘└─┬─┘                                                         └─┬─┘┌──────────────┐└─┬─┘          »
q_10: ──┤ U2(0,-π) ├───■─────────────────────────────────────────────────────────────■──┤ U2(π/2,-π/2) ├──■────────────»
        ├──────────┤                                                                    └──────────────┘               »
q_11: ──┤ U2(0,-π) ├───────────────────────────────────────────────────────────────────────────────────────────────────»
        └──────────┘                                                                                                   »
«      ┌───┐┌───────────────┐┌───┐┌──────────────┐                                            ┌───┐┌──────────────┐»
« q_0: ┤ X ├┤ Rz(-1.0*t[0]) ├┤ X ├┤ U2(π/2,-π/2) ├────────────────────────────────────────────┤ X ├┤ Rz(1.0*t[1]) ├»
«      └─┬─┘└───────────────┘└─┬─┘└────┬───┬─────┘                                       ┌───┐└─┬─┘└──────────────┘»
« q_1: ──■─────────────────────■───────┤ X ├─────────────────────────────────────────────┤ X ├──■──────────────────»
«                                      └─┬─┘      ┌───┐                             ┌───┐└─┬─┘                     »
« q_2: ──────────────────────────────────■────────┤ X ├─────────────────────────────┤ X ├──■───────────────────────»
«                                                 └─┬─┘┌───┐                   ┌───┐└─┬─┘                          »
« q_3: ─────────────────────────────────────────────■──┤ X ├───────────────────┤ X ├──■────────────────────────────»
«                   

### BQSKit compiler

BQSKit can efficiently simplify a deep circuit, but the parameters must be assigned.

It takes a few minutes to compile a circuit of depth ~ 10000.

In [97]:
from bqskit import compile, Circuit
from random import random
from numpy import pi
import os

def bqs_compile(circ, params):
    
    circ_paramed = circ.assign_parameters(params)
    
    bqs_temp = 'uccsd_bqs_temp.qasm'
    with open(bqs_temp, 'w') as file:
        file.write(circ_paramed.qasm())
    
    bqskit_rep_circ = Circuit.from_file(bqs_temp)
    bqskit_comp_circ = compile(bqskit_rep_circ, optimization_level=3)
    circ_bqs = QuantumCircuit.from_qasm_str(bqskit_comp_circ.to('qasm'))

    os.remove(bqs_temp)

    return circ_bqs

params = [0.0] * uccsd_lv3.num_parameters
# params = [2*pi*random() for i in range(uccsd_lv3.num_parameters)]

circ_bqs = bqs_compile(uccsd_lv3, params)

circ_bqs_ionq = transpile(circ_bqs, fakeionq, optimization_level=3)
# circ_bqs_huayi = transpile(circ_bqs, fakehuayi, optimization_level=3) # skipped because num_qubits of ansatz > num_qubits in Huayi
circ_bqs_montreal = transpile(circ_bqs, fakemontreal, optimization_level=3)

print("=== BQSKit simplified circuit ===")
print(circ_bqs.draw(fold=140))

print("=== BQSKit simplified circuit with IonQ backend ===")
print(circ_bqs_ionq.draw(fold=140, idle_wires=False))
# print("=== BQSKit simplified circuit with Huayi backend ===")
# print(circ_bqs_huayi.draw(fold=140, idle_wires=False))
print("=== BQSKit simplified circuit with Monrteal backend ===")
print(circ_bqs_montreal.draw(fold=140, idle_wires=False))

=== BQSKit simplified circuit ===
      ┌───────────────────────────┐                                                                 
 q_0: ┤ U3(3.1416,3.6494,0.50779) ├─────────────────────────────────────────────────────────────────
      └┬──────────────────────────┤                                                                 
 q_1: ─┤ U3(3.1416,3.2111,6.3527) ├─────────────────────────────────────────────────────────────────
       ├──────────────────────────┤                                                                 
 q_2: ─┤ U3(3.1416,7.5056,10.647) ├─────────────────────────────────────────────────────────────────
       ├─────────────────────────┬┘                                                                 
 q_3: ─┤ U3(3.1416,1.0944,4.236) ├──────────────────────────────────────────────────────────────────
       └─────────────────────────┘                                                                  
 q_4: ───────────────────────────────────────────────────

## Tapering

In [103]:
# Z2-symmetry tapering with Qiskit

from qiskit.quantum_info import SparsePauliOp
from qiskit.quantum_info.analysis import Z2Symmetries

z2sym = Z2Symmetries.find_z2_symmetries(qubit_ham)
print(z2sym)
 
tapered_ham = z2sym.taper(qubit_ham)[0]
print(tapered_ham.num_qubits, "qubits remained after Z2 tapering")

Z2 symmetries:
Symmetries:
IZZIIIZIIZZZ
IIZIIIIIZIII
IZIIIIIZIIII
ZZZZZZIIIIII
Single-Qubit Pauli X:
IIIIIIIIIIIX
IIIIIIIIXIII
IIIIIIIXIIII
IIIIIXIIIIII
Cliffords:
SparsePauliOp(['IZZIIIZIIZZZ', 'IIIIIIIIIIIX'],
              coeffs=[0.70710678+0.j, 0.70710678+0.j])
SparsePauliOp(['IIZIIIIIZIII', 'IIIIIIIIXIII'],
              coeffs=[0.70710678+0.j, 0.70710678+0.j])
SparsePauliOp(['IZIIIIIZIIII', 'IIIIIIIXIIII'],
              coeffs=[0.70710678+0.j, 0.70710678+0.j])
SparsePauliOp(['ZZZZZZIIIIII', 'IIIIIXIIIIII'],
              coeffs=[0.70710678+0.j, 0.70710678+0.j])
Qubit index:
[0, 3, 4, 6]
Tapering values:
  - Possible values: [1, 1, 1, 1], [1, 1, 1, -1], [1, 1, -1, 1], [1, 1, -1, -1], [1, -1, 1, 1], [1, -1, 1, -1], [1, -1, -1, 1], [1, -1, -1, -1], [-1, 1, 1, 1], [-1, 1, 1, -1], [-1, 1, -1, 1], [-1, 1, -1, -1], [-1, -1, 1, 1], [-1, -1, 1, -1], [-1, -1, -1, 1], [-1, -1, -1, -1]
8 qubits remained after Z2 tapering


## Grouping observables

In [184]:
# Generate the grouped observables of the target Hamiltonian
# output = [group1, group2, ...]
# each group = SparsePauliOp([PauliStr1, PauliStr2, ...], coeffs=[c1, c2, ...])

# Grouping method: Qiskit built-in group_commuting()
# Input includes the circuit, such that the anscilla qubits are filled with 'I'

def grouping_observables(hamiltonian, circuit):
    
    def rerange(op, maptable):
        num_qubits_device = circuit.num_qubits
        num_qubits_op = len(op)
        newstr = list('I'*num_qubits_device)
        for k,v in maptable.items():
            newstr[v] = op[k]
            # newstr[num_qubits_device-1-v] = op[num_qubits_op-1-k] # why reverse its order? according to Fudan's group
        return ''.join(newstr)
        
    grouped_ham = hamiltonian.group_commuting()

    qubits = circuit.layout.initial_layout.get_virtual_bits()
    maptable = {}
    for q in qubits:
        if 'ancilla' not in q.register.name:
            maptable[q.index] = qubits[q]
    
    grouped_observables = []
    for partial_ham in grouped_ham:
        ops = []
        for h in partial_ham:
            op = h.paulis.to_labels()[0]
            ops.append(rerange(op, maptable))
        grouped_observables.append(SparsePauliOp(ops, partial_ham.coeffs))

    return grouped_observables


In [190]:
# Qiskit built-in group_commuting

# grouped_ham = tapered_ham.group_commuting()

c_montreal = transpile(ansatz_effsu2, backend=fakemontreal, optimization_level=3)

grouped_observables = grouping_observables(tapered_ham, c_montreal)

print(len(grouped_observables), "groups are found")
print("{:>2}   {:>4}   {:<25}".format("id", "size", "max[abs(coeffs)]"))
for i,g in enumerate(grouped_observables):
    print("{:>2}  {:>4}   {:<25}".format(i,g.size,abs(max(g.coeffs, key=abs))))

35 groups are found
id   size   max[abs(coeffs)]         
 0    56   50.673827620692286       
 1    32   0.21924192058109698      
 2    30   0.18236945859975423      
 3    28   0.08213155786112081      
 4    32   0.21924192058109698      
 5    18   0.03074234323404705      
 6    16   0.015171505981391114     
 7    16   0.0171740305529211       
 8    30   0.18236945859975445      
 9    16   0.015171505981391114     
10    16   0.020493277836629003     
11    16   0.00541130285539375      
12    28   0.08213155786112084      
13    16   0.0171740305529211       
14    16   0.00541130285539375      
15    16   0.03461532759901961      
16    16   0.017348500353716146     
17    16   0.0538580239748233       
18    16   0.06485953217640462      
19     8   0.039235655683853364     
20     8   0.008452043966135038     
21     8   0.010412704013151955     
22     8   0.010075879017920673     
23     8   0.039235655683853364     
24     8   0.008452043966135038     
25     8   0.0104

/tmp/ipykernel_4098318/737754269.py:23: DeprecationWarning: The property ``qiskit.circuit.bit.Bit.register`` is deprecated as of qiskit-terra 0.17. It will be removed no earlier than 3 months after the release date. Instead, use :meth:`~qiskit.circuit.quantumcircuit.QuantumCircuit.find_bit` to find all the containing registers within a circuit and the index of the bit within the circuit.
  if 'ancilla' not in q.register.name:
/tmp/ipykernel_4098318/737754269.py:24: DeprecationWarning: The property ``qiskit.circuit.bit.Bit.index`` is deprecated as of qiskit-terra 0.17. It will be removed no earlier than 3 months after the release date. Instead, use :meth:`~qiskit.circuit.quantumcircuit.QuantumCircuit.find_bit` to find all the containing registers within a circuit and the index of the bit within the circuit.
  maptable[q.index] = qubits[q]


In [196]:
from qiskit_aer.noise.noise_model import NoiseModel
from qiskit_aer.primitives import Estimator

estimator = Estimator(
    backend_options = {
        'method': 'statevector',
        'device': 'CPU',
        'noise_model': NoiseModel.from_backend(fakemontreal)
    },
    run_options = {
        'shots': 2000,
        'seed': 114514,
    },
    skip_transpilation=True
)

def expect_hamiltonian(params, observables, estimator, circuit):
    result = 0.0
    for observables in grouped_observables:
        job = estimator.run(c_montreal, observables, params)
        result += job.result().values[0]
    print(result)
    return result


params = [2*pi*random() for i in range(c_montreal.num_parameters)]

# expect_hamiltonian(params, grouped_observables, estimator, c_montreal)

In [198]:
from scipy.optimize import minimize
Optimum = minimize(expect_hamiltonian,
                   params,
                   args=(grouped_observables, estimator, c_montreal),
                   method='COBYLA',
                   options={"maxiter":5000,"rhobeg":np.pi,'eps':0.000005})

/home/zhouyijia/anaconda3/envs/vqe/lib/python3.11/site-packages/scipy/optimize/_minimize.py:716: OptimizeWarning: Unknown solver options: eps
  res = _minimize_cobyla(fun, x0, args, constraints, callback=callback,


-50.115100315081804
-50.92758001559634
-48.0152524728844
-51.849099296305575
-49.45139531139222
-51.79567075276187
-53.16520158751026
-52.524261229460144
-50.849818451268405
-52.49124047428001
-52.71319989682457
-53.24252901196665
-50.66670913599213
-50.36196535892858
-50.2443704007582
-52.67260110350068
-51.17818172520178
-50.2789542266873
-53.066050768277826
-52.25487531450456
-50.604624740249605
-52.69068284198326
-53.01330758607116
-53.1636560763415
-52.50359869834906
-54.657219025529734
-52.45740045278123
-50.579037008508905
-61.91651457003991
-56.94740691718808
-59.21969442933943
-56.49118131183504
-57.87371373800012
-63.628921223080425
-61.927853165655705
-65.39567606803492
-62.62164340964359
-66.26617104780554
-66.3932323402058
-60.931128642114636
-62.69947357138441
-63.219913139234336
-65.77441095344803
-61.5081245921799
-65.5264470452509
-55.753099839189694
-62.66279865219826
-60.18704148715916
-51.17269841339126
-61.92807551910918
-65.46855136525203
-63.61064943479867
-65.75

In [204]:
Optimum.x

array([3.349031  , 3.91670558, 6.00812727, 4.49107288, 3.46448981,
       7.85960236, 3.2369223 , 4.25809534, 0.25368933, 3.30801792,
       5.96259547, 0.74736222, 0.78736846, 2.04204489, 4.27749407,
       4.25685245])